In [2]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from IPython.display import GeoJSON
import folium
import json

In [3]:
datameta = pd.read_csv('meta.csv')

In [4]:
datameta.head()

municipal  population_2007  population_2008  population_2009  \
0    medellin          2286126          2309689          2331389   
1   abejorral            20643            20944            21197   
2    abriaqui             2261             2290             2321   
3  alejandria             3935             4020             4096   
4       amaga            27996            28331            28624   

   population_2010  population_2011  population_2012  population_2013  \
0          2353410          2379920          2410046          2428850   
1            21355            20973            20067            19732   
2             2353             2386             2424             2471   
3             4171             4244             4337             4419   
4            28839            28776            28371            28259   

   population_2014  population_2015  ...  age_30_and_up  illiterate  \
0          2436071          2431666  ...          56.16        3.17   
1            19796            19897  ...          57.55        9.89   
2             2488             2514  ...          56.09        6.72   
3             4467             4511  ...          55.77        8.75   
4            28432            28691  ...          55.50        7.68   

   secondary_education  employed  unemployed    men  women  \
0                67.43     43.23        5.64  47.01  52.99   
1                33.65     39.60        0.89  51.93  48.07   
2                45.72     36.78        1.85  54.24  45.76   
3                38.79     37.07        1.25  49.80  50.20   
4                51.67     39.21        3.36  49.37  50.63   

   households_without_water_access  households_without_internet_access  \
0                             1.44                               29.47   
1                            21.87                               56.27   
2                            24.03                               62.35   
3                            17.06                               54.61   
4                             3.31                               56.12   

   houses_per_km2  
0     2102.057895  
1       11.945674  
2        2.548276  
3        9.092715  
4      102.752941  

[5 rows x 40 columns]

In [5]:
dataweather = pd.read_csv('weather.csv')

In [6]:
dataweather.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1121 entries, 0 to 1120
Columns: 289 entries, municipal to precipitation_dec_18
dtypes: float64(288), object(1)
memory usage: 2.5+ MB


In [97]:
import json
import folium
import numpy as np
import matplotlib.pyplot as plt

# Load the GeoJSON data
with open('master.geojson') as f:
    geojson_data = json.load(f)

# Create a base map centered on Colombia
colombia_map = folium.Map(location=[4.5709, -74.2973], zoom_start=5)

# Create a colormap
cmap = plt.get_cmap('YlOrRd')

# Function to determine color based on cases/population ratio
def get_color(cases, pop):
    if pop == 0 or cases is None:  # Handle division by zero or undefined cases
        return "gray"  # Undefined
    ratio = np.round(cases / pop, 5)
    # Normalize the ratio to range between 0 and 1
    normalized_ratio = min(ratio, 1)
    rgba_color = cmap(normalized_ratio / .01)  # Get the color from the colormap
    # Convert RGBA to HEX
    hex_color = "#{:02x}{:02x}{:02x}".format(int(rgba_color[0] * 255), 
                                              int(rgba_color[1] * 255), 
                                              int(rgba_color[2] * 255))

    return hex_color

# Add a GeoJSON overlay for Colombia with specific styling
folium.GeoJson(
    geojson_data,
    name='Colombia',
    style_function=lambda feature: {
        'fillColor': get_color(feature['properties']['cases_2018'], 
                               feature['properties']['population_2018']),
        'color': 'black',  # Border color
        'weight': .5,
        'fillOpacity': 0.6,
    }
).add_to(colombia_map)

# Add Layer Control
folium.LayerControl().add_to(colombia_map)

# Create a legend
legend_html = '''
<div style="position: fixed; 
            bottom: 50px; left: 50px; width: 200px; height: 70px; 
            border:2px solid grey; z-index:9999; font-size:14px;
            background-color:white;">
    <b>Cases per Population Ratio</b><br>
    <div style="width: 100%; height: 20px; background: linear-gradient(to right, 
    #FFFF00, #FF0000);"></div>
    <i style="color:gray;">0.0----0.0033----0.0066----0.01+</i>
</div>
'''

# Add the legend to the map
colombia_map.get_root().html.add_child(folium.Element(legend_html))

# Save the map to an HTML file
colombia_map.save('colombia_map.html')


In [98]:
colombia_map